## Imports

In [2]:
import os
import string
import re
from nltk.stem import *
import nltk
import itertools
import math
import operator
import sys
from statistics import mean
from tika import parser
import re

## Reading paragraphs and mapping them to documents

In [3]:
list_text = []  #list of all paragraphs
para_list = {}  #map from para : doc
list_doc = []   #list of names of all txt input files
file1 = open('myfile.txt', 'w',encoding = 'utf-8')
doc = 0
for root,dir,files in os.walk('txt_files2'):
    for file in files:
        # print(os.path.join(root,file))
        if(os.path.join(root,file).endswith('.txt')):
            # path = root.split('/')
            print(file)
            list_doc.append(file)
            doc = len(list_doc)-1
            s = ""
            i = 0
            file1 = open(os.path.join(root,file),encoding='utf8')
            text = file1.read()
            text = re.split(r"\n\s+",text)
            for para in text:
                para = para.split()
                # print("NEW PARA ___",para)
                for word in para:
                    # print(word+'WORD')
                    s= s+ " " + word
                    i+=1
                    if(i>=100 and s[-1]=='.'):
                        list_text.append(s)
                        para_list[len(list_text)-1] = doc
                        s=""
                        i=0
                if(i<40): continue
                list_text.append(s)
                para_list[len(list_text)-1] = doc
                s=""
                i=0


1215E.2.txt
7thEditionPolicy.txt
AU127-1.txt
Business-Auto-Policy-CA0001-03-10.txt
PL-600003-87.txt
PP_00_01_06_98.txt
5105072011_booklet.txt
BRIT-PO-Policy-Wording-May-2016-1.txt
complete-property-owner-policy-wording-policies-incepting-or-renewing-from-010418-acom686-11.txt
eSols Property Owners Commercial Policy Wording 2018 Policies which incepted before 01 July.txt
Liberty-SECT-Policy-Wording.txt
Property-Owner-Policy-Wording.txt
Residential-Property-Owners-Policy-Wording-1910.txt
rsa_property_owners_policy_wording.txt


In [ ]:
len(list_text)

In [ ]:
list_doc

In [ ]:
para_list

## Tokenization and Normalisation

In [9]:
from nltk.corpus import stopwords
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Rishi\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [11]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Rishi\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [12]:
def lowercasify(data):
    return data.lower()


def clean_and_tokenise_text(text):
    # Remove apostrophes along with other punctuations
    translator = str.maketrans('', '', string.punctuation + "’")
    text = text.translate(translator)
    # Remove digits
    text = ''.join([char for char in text if not char.isdigit()])
    # Tokenize the cleaned text
    words = nltk.word_tokenize(text)
    return words


def get_stemmed_words(tokens):
    # Initialize Porter Stemmer object
    stemmer = PorterStemmer()
    # Apply stemming to each word in tokens
    stemmed_words = [stemmer.stem(word) for word in tokens]
    # Return the list of stemmed words
    return stemmed_words


def remove_stop_words(tokens):
    # Get the list of stop words for English language
    stop_words = stopwords.words('english')
    # Initialize an empty list to store non-stop words
    filtered_words = []
    # Iterate over each token in the input list
    for token in tokens:
        # Check if the token is not a stop word and its length is greater than 2 characters
        if token not in stop_words and len(token) > 2:
            # If the conditions are met, add the token to the list of non-stop words
            filtered_words.append(token)
    return filtered_words

In [13]:
def preprocess_data(list_text):
    dataDict = {}
    for i in range(len(list_text)):
        # Convert to lowercase
        preprocessed_list=lowercasify(list_text[i])
        # Tokenize and remove punctuations and digits
        tokens = clean_and_tokenise_text(preprocessed_list)
        # Remove stop words
        filtered_tokens = remove_stop_words(tokens)
        # Stem the remaining words
        stemmed_tokens = get_stemmed_words(filtered_tokens)
        # Remove stop words again
        filtered_tokens1 = remove_stop_words(stemmed_tokens)
        # Add preprocessed data to dictionary
        dataDict[i] = filtered_tokens1
    return dataDict

In [14]:
preprocessed_list_text = preprocess_data(list_text)
preprocessed_list_text

{0: ['ontario',
  'automobil',
  'polici',
  'oap',
  'owner',
  'polici',
  'approv',
  'superintend',
  'financi',
  'servic',
  'use',
  'standard',
  'owner',
  'polici',
  'june',
  'polici',
  'automobil',
  'insur',
  'polici',
  'written',
  'easi',
  'understand',
  'languag',
  'pleas',
  'read',
  'care',
  'know',
  'right',
  'oblig',
  'right',
  'oblig',
  'insur',
  'compani',
  'summari',
  'section',
  'polici',
  'detail',
  'coverag',
  'condit',
  'appli',
  'consult',
  'appropri',
  'section',
  'polici',
  'section',
  'introduct',
  'contain',
  'inform',
  'appli',
  'entir',
  'polici'],
 1: ['order',
  'understand',
  'cover',
  'cover',
  'coverag',
  'read',
  'section',
  'entir',
  'section',
  'polici',
  'deal',
  'specif',
  'coverag',
  'section',
  'automobil',
  'cover',
  'explain',
  'coverag',
  'avail',
  'describ',
  'automobil',
  'type',
  'automobil',
  'exampl',
  'newli',
  'acquir',
  'temporari',
  'substitut',
  'automobil',
  'specif'

## Inverted Index

In [15]:
def get_vocabulary(data):##
    tokens = []
    for token_list in data.values():
        tokens = tokens + token_list
    fdist = nltk.FreqDist(tokens)
    return list(fdist.keys())

def generate_inverted_index(data):
    all_words = get_vocabulary(data)
    index = {}
    for word in all_words:
        for doc, tokens in data.items():
            if word in tokens :
                if word in index.keys():
                    index[word].append(doc)
                else:
                    index[word] = [doc]
    return index

In [16]:
inverted_index = generate_inverted_index(preprocessed_list_text)

In [17]:
inverted_index

{'ontario': [0,
  3,
  4,
  5,
  9,
  14,
  16,
  22,
  27,
  29,
  80,
  86,
  93,
  108,
  129,
  130,
  134,
  140,
  141,
  143,
  147,
  232],
 'automobil': [0,
  1,
  2,
  3,
  4,
  5,
  6,
  8,
  9,
  10,
  11,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21,
  24,
  29,
  30,
  32,
  37,
  38,
  39,
  40,
  41,
  42,
  44,
  45,
  46,
  47,
  48,
  49,
  50,
  51,
  52,
  53,
  54,
  55,
  56,
  57,
  58,
  59,
  60,
  61,
  62,
  63,
  64,
  65,
  66,
  67,
  70,
  71,
  72,
  73,
  74,
  75,
  76,
  77,
  79,
  80,
  81,
  82,
  83,
  84,
  85,
  87,
  89,
  90,
  92,
  93,
  107,
  108,
  109,
  110,
  111,
  112,
  113,
  114,
  115,
  118,
  119,
  121,
  122,
  123,
  124,
  125,
  126,
  127,
  130,
  132,
  133,
  134,
  136,
  138,
  139,
  140,
  141,
  142,
  143,
  144,
  145,
  146,
  147,
  148,
  149,
  151,
  152,
  153,
  154,
  155,
  159,
  160,
  162,
  163,
  164,
  166,
  167,
  168,
  169,
  170,
  171,
  172,
  173,
  174,
  175,
  178,
  179,
  180

## Preprocess queries

In [18]:
query1 = 'insurance'

In [19]:
def preprocess_query(query):
    lowercase_query=lowercasify(query)
    query_tokens = clean_and_tokenise_text(lowercase_query)
    query_filtered_tokens = remove_stop_words(query_tokens)
    query_stemmed_tokens = get_stemmed_words(query_filtered_tokens)
    query_filtered_tokens1 = remove_stop_words(query_stemmed_tokens)
    return query_filtered_tokens1

In [20]:
query = "arbitration damages responsible owner investigation"
preprocessed_query = preprocess_query(query)
preprocessed_query

['arbitr', 'damag', 'respons', 'owner', 'investig']

In [32]:
def preprocess_queries(path):
    queriesDict = {}
    queries = open(path,'r').read().split('\n')
    i = 1
    for query in queries:
        tokens = tokenize_and_remove_punctuations(query)
        filtered_tokens = remove_stop_words(tokens)
        stemmed_tokens = stem_words(filtered_tokens)
        filtered_tokens1 = remove_stop_words(stemmed_tokens)
        queriesDict[i] = filtered_tokens1
        i+=1
    return queriesDict

## TF-IDF

In [25]:
def calculate_tf(tokens):
    tf_score = {}
    for token in tokens:
        tf_score[token] = tokens.count(token)/len(tokens)
    return tf_score

In [26]:
def calculate_idf(data):
    idf_score = {}
    N = len(data)
    all_words = get_vocabulary(data)
    for word in all_words:
        word_count = 0
        for token_list in data.values():
            if word in token_list:
                word_count += 1
        idf_score[word] = math.log10(N/word_count)
    return idf_score

def calculate_tfidf(data, idf_score):
    scores = {}
    for key,value in data.items():
        scores[key] = calculate_tf(value)
    for doc,tf_scores in scores.items():
        for token, score in tf_scores.items():
            tf = score
            idf = idf_score[token]
            tf_scores[token] = tf * idf
    return scores

In [27]:
def calculate_tfidf_query(query, idf_score):
    tf_score = calculate_tf(query)
    # for key, tf_scores in scores.items():
    for token, score in tf_score.items():
        idf = 0
        tf = score
        if token in idf_score.keys():
            idf = idf_score[token]
        tf_score[token] = tf * idf
    return tf_score

In [28]:
calculate_tf(preprocessed_query)

{'arbitr': 0.2, 'damag': 0.2, 'respons': 0.2, 'owner': 0.2, 'investig': 0.2}

In [33]:
query = "will you pay or reimburse if there is collision while racing or stunting?"
preprocessed_query = preprocess_query(query)
preprocessed_query

['pay', 'reimburs', 'collis', 'race', 'stunt']

In [34]:
query = "What is the maximum amount payable for Rent Guarantee Insurance?"
preprocessed_query = preprocess_query(query)
preprocessed_query

['maximum', 'amount', 'payabl', 'rent', 'guarante', 'insur']

In [35]:
idf_scores = calculate_idf(preprocessed_list_text)
scores = calculate_tfidf(preprocessed_list_text,idf_scores)#dict of dict storing tf-idf score of each token in each para
query_scores = calculate_tfidf_query(preprocessed_query,idf_scores)#dict 'word' : 'tf_idf'

In [38]:
scores

{0: {'ontario': 0.04213605907866797,
  'automobil': 0.048760330489116314,
  'polici': 0.07943287332059285,
  'oap': 0.06255552349353513,
  'owner': 0.05275426110415822,
  'approv': 0.041395106904366014,
  'superintend': 0.06255552349353513,
  'financi': 0.028277326885570414,
  'servic': 0.01869691370119605,
  'use': 0.014556839854472769,
  'standard': 0.0362335101440801,
  'june': 0.06845807242812299,
  'insur': 0.006738793912502691,
  'written': 0.02333983721902532,
  'easi': 0.054752778225455954,
  'understand': 0.04384488605354837,
  'languag': 0.04885022929086809,
  'pleas': 0.0343333138105888,
  'read': 0.03662965496934063,
  'care': 0.03388105294649677,
  'know': 0.04175752662385647,
  'right': 0.04156854626177589,
  'oblig': 0.06480441580772617,
  'compani': 0.020721427250981844,
  'summari': 0.045397459505462576,
  'section': 0.033973402438268,
  'detail': 0.026019781138232067,
  'coverag': 0.016762231323155043,
  'condit': 0.015973884004106,
  'appli': 0.030504751009424715,
  

In [39]:
query_scores

{'maximum': 0.20888593178424622,
 'amount': 0.12881000082783306,
 'payabl': 0.19181959649902572,
 'rent': 0.18610222463736148,
 'guarante': 0.3962363902545726,
 'insur': 0.028639874128136435}

In [40]:
# Calculate cosine similarity between query and documents
doc_sim = {}

for term,term_val in query_scores.items():
    if term in inverted_index.keys():
        # print(term,term_val)
        docs = inverted_index[term]
        # print(docs)
        for doc in docs:
            doc_length = math.sqrt(sum(x ** 2 for x in scores[doc].values()))
            doc_score = scores[doc][term]#tf_idf score of term in the doc
            query_score = term_val
            query_length = 1
            query_length = math.sqrt(sum(x ** 2 for x in query_scores.values()))
            cosine_sim = (doc_score * query_score) / (doc_length * query_length)
            if doc in doc_sim.keys():
                doc_sim[doc] += cosine_sim
            else:
                doc_sim[doc] = cosine_sim
ranked = sorted(doc_sim.items(), key=operator.itemgetter(1), reverse=True)
# ranked[0]
for i in range(min(len(ranked),5)):
    print("DOCUMENT = ",list_doc[para_list[ranked[i][0]]],"\n",list_text[ranked[i][0]]+"\n\n")

# scores
# type(ranked)

DOCUMENT =  eSols Property Owners Commercial Policy Wording 2018 Policies which incepted before 01 July.txt 
  You must take all steps to comply with any regulations and keep evidence of compliance. Maximum Amount Payable: £50,000 Excess: Nil Section 4 - Rent Guarantee Insurance This section of cover only applies where You have paid the appropriate additional premium and cover for Rent Guarantee Insurance is shown separately from Legal Expenses Insurance as insured on Your policy schedule. What is Insured


DOCUMENT =  eSols Property Owners Commercial Policy Wording 2018 Policies which incepted before 01 July.txt 
  Maximum Amount Payable The maximum payable in respect of an Insured Event. This amount is shown under each section of cover. Period of Insurance The period of insurance shown in the schedule. Rent The monthly amount payable by the Tenant to You as set out in the Tenancy Agreement.


DOCUMENT =  Liberty-SECT-Policy-Wording.txt 
  Rent Payable shall mean loss of rent payable 

In [41]:
print(query_score)


0.028639874128136435


In [42]:
calculate_tfidf_query(preprocessed_query,idf_scores)

{'maximum': 0.20888593178424622,
 'amount': 0.12881000082783306,
 'payabl': 0.19181959649902572,
 'rent': 0.18610222463736148,
 'guarante': 0.3962363902545726,
 'insur': 0.028639874128136435}

## Word2Vec

In [44]:
from gensim.models import Word2Vec

In [46]:
paras = list_text.copy()
for i in range(len(paras)):
    paras[i] = lowercasify(paras[i])
    paras[i] = clean_and_tokenise_text(paras[i])
    paras[i] = remove_stop_words(paras[i])
    paras[i] = remove_stop_words(paras[i])
    paras[i] = get_stemmed_words(paras[i])
    paras[i] = remove_stop_words(paras[i])
# paras = [nltk.word_tokenize(sentence) for sentence in paras]

In [50]:
paras

[['ontario',
  'automobil',
  'polici',
  'oap',
  'owner',
  'polici',
  'approv',
  'superintend',
  'financi',
  'servic',
  'use',
  'standard',
  'owner',
  'polici',
  'june',
  'polici',
  'automobil',
  'insur',
  'polici',
  'written',
  'easi',
  'understand',
  'languag',
  'pleas',
  'read',
  'care',
  'know',
  'right',
  'oblig',
  'right',
  'oblig',
  'insur',
  'compani',
  'summari',
  'section',
  'polici',
  'detail',
  'coverag',
  'condit',
  'appli',
  'consult',
  'appropri',
  'section',
  'polici',
  'section',
  'introduct',
  'contain',
  'inform',
  'appli',
  'entir',
  'polici'],
 ['order',
  'understand',
  'cover',
  'cover',
  'coverag',
  'read',
  'section',
  'entir',
  'section',
  'polici',
  'deal',
  'specif',
  'coverag',
  'section',
  'automobil',
  'cover',
  'explain',
  'coverag',
  'avail',
  'describ',
  'automobil',
  'type',
  'automobil',
  'exampl',
  'newli',
  'acquir',
  'temporari',
  'substitut',
  'automobil',
  'specif',
  'c

In [24]:
w2v_model = Word2Vec(paras, min_count=2,window=5, sg=1,workers=2)

In [25]:
words = list(w2v_model.wv.index_to_key)

In [26]:
words

['insur',
 'damag',
 'polici',
 'loss',
 'person',
 'claim',
 'properti',
 'section',
 'cover',
 'shall',
 'liabil',
 'pay',
 'limit',
 'legal',
 'auto',
 'respect',
 'provid',
 'cost',
 'coverag',
 'use',
 'caus',
 'includ',
 'period',
 'condit',
 'amount',
 'may',
 'expens',
 'premis',
 'part',
 'result',
 'appli',
 'aris',
 'build',
 'act',
 'one',
 'injuri',
 'servic',
 'requir',
 'busi',
 'reason',
 'time',
 'within',
 'automobil',
 'must',
 'indemn',
 'schedul',
 'rent',
 'vehicl',
 'premium',
 'compani',
 'payment',
 'incur',
 'addit',
 'accid',
 'contract',
 'mean',
 'inform',
 'follow',
 'day',
 'event',
 'right',
 'date',
 'shown',
 'work',
 'term',
 'repair',
 'exclus',
 'equip',
 'employe',
 'made',
 'employ',
 'bodili',
 'agre',
 'relat',
 'unless',
 'law',
 'connect',
 'data',
 'state',
 'agreement',
 'replac',
 'oper',
 'repres',
 'notic',
 'subject',
 'declar',
 'make',
 'proceed',
 'indemnifi',
 'sum',
 'payabl',
 'extens',
 'purpos',
 'respons',
 'occur',
 'valu',
 'w

In [33]:
import numpy as np
def get_embedding_w2v(doc_tokens):
    embeddings = []
    if len(doc_tokens)<1:
        return np.zeros(300)
    else:
        for tok in doc_tokens:
            if tok in words:
                embeddings.append(w2v_model.wv.word_vec(tok))
            else:
                embeddings.append(np.random.rand(100))
        # mean the vectors of individual words to get the vector of the document
        return np.mean(embeddings, axis=0)

In [77]:
query = "Will insurance pay for accident which occurs while your auto is being operated by a household member who is not listed as the operator of this policy"
preprocessed_query = preprocess_query(query)
preprocessed_query

['insur',
 'pay',
 'accid',
 'occur',
 'auto',
 'oper',
 'household',
 'member',
 'list',
 'oper',
 'polici']

In [78]:
query_score = get_embedding_w2v(preprocessed_query)
print(query_score)

[ 0.5443457  -0.1505713  -0.0163159  -0.22199711  0.06457342 -0.29319215
  0.22579317  0.34790722  0.13010022 -0.21805495  0.20633912 -0.09242837
 -0.02989082 -0.03138395 -0.07287954  0.16982955  0.2202728   0.17124918
 -0.03711337 -0.20221645  0.05243216  0.11647136  0.17286745 -0.4898738
 -0.05019519 -0.07206729  0.06009891  0.15394324  0.11966991 -0.16646625
  0.11308543 -0.13036597  0.4176191  -0.02165512 -0.005207   -0.17396693
  0.02927857  0.10332751  0.11482334 -0.30973718  0.14074701  0.07675224
 -0.0094966   0.08672894  0.27844438  0.3440946  -0.20254272  0.03295606
 -0.06266401 -0.00482103 -0.2913495   0.16518216 -0.13519779  0.04212901
 -0.12999889  0.3267639   0.3314699   0.07283394  0.20564224  0.03665172
  0.0372479  -0.02444707  0.2520566  -0.03791736 -0.23672312  0.4023939
  0.05888215 -0.06887506 -0.31692445 -0.03718952 -0.21681923  0.02437309
  0.06871796  0.10060227  0.34002346 -0.2633416  -0.0338288  -0.02921328
 -0.4772684  -0.1005935  -0.15713806  0.2920966   0.0

C:\Users\ssbad\AppData\Local\Temp\ipykernel_4020\1688578791.py:9: DeprecationWarning: Call to deprecated `word_vec` (Use get_vector instead).
  embeddings.append(w2v_model.wv.word_vec(tok))


In [71]:

para_scores = []
for x in preprocessed_list_text.values():
    para_scores.append(get_embedding_w2v(x))
para_scores

C:\Users\ssbad\AppData\Local\Temp\ipykernel_4020\1688578791.py:9: DeprecationWarning: Call to deprecated `word_vec` (Use get_vector instead).
  embeddings.append(w2v_model.wv.word_vec(tok))


[array([ 0.33401655, -0.18131193, -0.15750255, -0.17967817,  0.01444708,
        -0.17873746,  0.14417291,  0.40512642,  0.13228873, -0.01725732,
         0.11596018,  0.05986049, -0.03785134, -0.03123893, -0.11759272,
         0.07732928,  0.32624342,  0.21870787,  0.00167299, -0.10702896,
        -0.06419145, -0.01267262,  0.12844186, -0.37510109,  0.05543904,
        -0.09011187, -0.03509401,  0.18272387,  0.01963839, -0.06650743,
         0.24176404, -0.08778138,  0.22507096, -0.04480069,  0.0111744 ,
        -0.1420523 , -0.02173793,  0.07171841,  0.11024754, -0.15713949,
         0.17502438,  0.04733746,  0.20918835,  0.14544995,  0.13828977,
         0.05670125, -0.14000109,  0.16065628, -0.12366398, -0.05014705,
        -0.29659625,  0.02348722, -0.06750797,  0.01128279, -0.19849412,
         0.29983569,  0.15637246, -0.06665365,  0.02993132,  0.09401294,
         0.21029025, -0.10687532,  0.3897602 , -0.02561804, -0.21290096,
         0.2409097 ,  0.24169959,  0.24149727, -0.3

In [72]:
from sklearn.metrics.pairwise import cosine_similarity
query_score.shape


(100,)

In [79]:
doc_sim = {}
# query_score = query_score.reshape(-1,1)
for i in range(len(para_scores)):
        sumq = 0
        sump = 0
        sumcross = 0
        for x in range(100):
                sump+=para_scores[i][x]*para_scores[i][x]
                sumq+=query_score[x]*query_score[x]
                sumcross+=query_score[x]*para_scores[i][x]
        doc_sim[i] = sumcross/(math.sqrt(sump*sumq))

ranked = sorted(doc_sim.items(), key=operator.itemgetter(1), reverse=True)
# ranked[0]
for i in range(min(len(ranked),5)):
    print("DOCUMENT = ",list_doc[para_list[ranked[i][0]]],"\n",list_text[ranked[i][0]]+"\n\n")



DOCUMENT =  7thEditionPolicy.txt 
  We will not pay for a loss for an accident which occurs while your auto is being operated by a household member who is not listed as an operator of this policy. Payment is withheld when the household member, if listed, would require the payment of additional premium on this policy because: 1. the household member would be classified as an inexperienced operator, or


DOCUMENT =  PP_00_01_06_98.txt 
  3. Which is a hit-and-run vehicle whose operator or owner cannot be identified and which hits: a. You or any "family member"; b. A vehicle which you or any "family mem- ber" are "occupying"; or c. "Your covered auto". 4. To which a bodily injury liability bond or policy applies at the time of the accident but the bonding or insuring company: a. Denies coverage; or b. Is or becomes insolvent. However, "uninsured motor vehicle" does not in- clude any vehicle or equipment: 1. Owned by or furnished or available for the regular use of you or any "family membe